In [1]:
import requests
from pymongo import MongoClient, UpdateOne
from datetime import datetime
import time
from tqdm.notebook import tqdm  # Use tqdm for Jupyter Notebook


# URL to fetch satellite data
url = 'https://celestrak.org/NORAD/elements/gp.php?GROUP=active&FORMAT=json'

# Fetch data from URL
response = requests.get(url)
satellite_data = response.json()

# Connect to MongoDB
client = MongoClient('mongodb://localhost:27017/')
db = client['satellite_db']
collection = db['active_satellites']

# Prepare the data for MongoDB
bulk_operations = []

print(satellite_data)

[{'OBJECT_NAME': 'CALSPHERE 1', 'OBJECT_ID': '1964-063C', 'EPOCH': '2024-06-07T00:43:48.787392', 'MEAN_MOTION': 13.7505863, 'ECCENTRICITY': 0.002749, 'INCLINATION': 90.2051, 'RA_OF_ASC_NODE': 55.164, 'ARG_OF_PERICENTER': 16.0259, 'MEAN_ANOMALY': 90.7741, 'EPHEMERIS_TYPE': 0, 'CLASSIFICATION_TYPE': 'U', 'NORAD_CAT_ID': 900, 'ELEMENT_SET_NO': 999, 'REV_AT_EPOCH': 96963, 'BSTAR': 0.00108, 'MEAN_MOTION_DOT': 1.043e-05, 'MEAN_MOTION_DDOT': 0}, {'OBJECT_NAME': 'CALSPHERE 2', 'OBJECT_ID': '1964-063E', 'EPOCH': '2024-06-06T11:25:35.365728', 'MEAN_MOTION': 13.52800065, 'ECCENTRICITY': 0.0017205, 'INCLINATION': 90.2211, 'RA_OF_ASC_NODE': 58.7544, 'ARG_OF_PERICENTER': 212.7496, 'MEAN_ANOMALY': 322.5087, 'EPHEMERIS_TYPE': 0, 'CLASSIFICATION_TYPE': 'U', 'NORAD_CAT_ID': 902, 'ELEMENT_SET_NO': 999, 'REV_AT_EPOCH': 75611, 'BSTAR': 8.3046e-05, 'MEAN_MOTION_DOT': 6.4e-07, 'MEAN_MOTION_DDOT': 0}, {'OBJECT_NAME': 'LCS 1', 'OBJECT_ID': '1965-034C', 'EPOCH': '2024-06-06T14:22:47.303040', 'MEAN_MOTION': 9.89

In [ ]:
for sat in tqdm(satellite_data, desc="Processing satellites"):
    epoch = sat['EPOCH']
    
    position = {
        "EPOCH": epoch,
        "MEAN_MOTION": sat['MEAN_MOTION'],
        "ECCENTRICITY": sat['ECCENTRICITY'],
        "INCLINATION": sat['INCLINATION'],
        "RA_OF_ASC_NODE": sat['RA_OF_ASC_NODE'],
        "ARG_OF_PERICENTER": sat['ARG_OF_PERICENTER'],
        "MEAN_ANOMALY": sat['MEAN_ANOMALY'],
        "EPHEMERIS_TYPE": sat['EPHEMERIS_TYPE'],
        "CLASSIFICATION_TYPE": sat['CLASSIFICATION_TYPE'],
        "NORAD_CAT_ID": sat['NORAD_CAT_ID'],
        "ELEMENT_SET_NO": sat['ELEMENT_SET_NO'],
        "REV_AT_EPOCH": sat['REV_AT_EPOCH'],
        "BSTAR": sat['BSTAR'],
        "MEAN_MOTION_DOT": sat['MEAN_MOTION_DOT'],
        "MEAN_MOTION_DDOT": sat['MEAN_MOTION_DDOT'],
        "timestamp": int(time.time())  # Add the current timestamp
    }
    
    query = {
        "OBJECT_ID": sat['OBJECT_ID'],
        "positions": {"$not": {"$elemMatch": {"EPOCH": epoch}}}
    }
    
    update = {
        "$set": {"OBJECT_NAME": sat['OBJECT_NAME'], "OBJECT_ID": sat['OBJECT_ID']},
        "$push": {"positions": position}
    }
    bulk_operations.append(UpdateOne(query, update, upsert=True))


In [ ]:

# Execute the bulk write operation
if bulk_operations:
    result = collection.bulk_write(bulk_operations)
    print(f"Matched: {result.matched_count}, Modified: {result.modified_count}, Upserted: {result.upserted_count}")
else:
    print("No data to update")

print("Data inserted/updated successfully")
